In [3]:
import numpy as np
import matplotlib.pyplot as plt
import math
import pandas as pd

import seaborn as sns
import statsmodels.api as sm #this line is now always in our opener
from patsy import dmatrices

from nba_api.stats.endpoints import teamgamelogs
from nba_api.stats.static import teams
nba_teams = teams.get_teams()
teamIDs = [team['id'] for team in nba_teams]

In [61]:
games = []
games.append(pd.read_csv(r'.\data\2014-15.csv', index_col=0))
games.append(pd.read_csv(r'.\data\2015-16.csv', index_col=0))
games.append(pd.read_csv(r'.\data\2016-17.csv', index_col=0))
games.append(pd.read_csv(r'.\data\2017-18.csv', index_col=0))
games.append(pd.read_csv(r'.\data\2018-19.csv', index_col=0))
games.append(pd.read_csv(r'.\data\2019-20.csv', index_col=0))
games.append(pd.read_csv(r'.\data\2020-21.csv', index_col=0))
games[2].head(50)

SEASON_YEAR     TEAM_ID TEAM_ABBREVIATION               TEAM_NAME  \
0      2016-17  1610612739               CLE     Cleveland Cavaliers   
2      2016-17  1610612752               NYK         New York Knicks   
1      2016-17  1610612759               SAS       San Antonio Spurs   
0      2016-17  1610612762               UTA               Utah Jazz   
2      2016-17  1610612757               POR  Portland Trail Blazers   
1      2016-17  1610612744               GSW   Golden State Warriors   
6      2016-17  1610612745               HOU         Houston Rockets   
7      2016-17  1610612748               MIA              Miami Heat   
8      2016-17  1610612750               MIN  Minnesota Timberwolves   
9      2016-17  1610612765               DET         Detroit Pistons   
10     2016-17  1610612758               SAC        Sacramento Kings   
11     2016-17  1610612751               BKN           Brooklyn Nets   
12     2016-17  1610612760               OKC   Oklahoma City Thunder   
3      2016-17  1610612763               MEM       Memphis Grizzlies   
3      2016-17  1610612766               CHA       Charlotte Hornets   
5      2016-17  1610612742               DAL        Dallas Mavericks   
4      2016-17  1610612761               TOR         Toronto Raptors   
4      2016-17  1610612743               DEN          Denver Nuggets   
5      2016-17  1610612754               IND          Indiana Pacers   
6      2016-17  1610612755               PHI      Philadelphia 76ers   
7      2016-17  1610612753               ORL           Orlando Magic   
8      2016-17  1610612749               MIL         Milwaukee Bucks   
9      2016-17  1610612747               LAL      Los Angeles Lakers   
10     2016-17  1610612740               NOP    New Orleans Pelicans   
11     2016-17  1610612756               PHX            Phoenix Suns   
12     2016-17  1610612738               BOS          Boston Celtics   
13     2016-17  1610612757               POR  Portland Trail Blazers   
16     2016-17  1610612741               CHI           Chicago Bulls   
14     2016-17  1610612758               SAC        Sacramento Kings   
15     2016-17  1610612737               ATL           Atlanta Hawks   
15     2016-17  1610612764               WAS      Washington Wizards   
14     2016-17  1610612759               SAS       San Antonio Spurs   
13     2016-17  1610612738               BOS          Boston Celtics   
16     2016-17  1610612746               LAC             LA Clippers   
18     2016-17  1610612754               IND          Indiana Pacers   
19     2016-17  1610612747               LAL      Los Angeles Lakers   
20     2016-17  1610612766               CHA       Charlotte Hornets   
21     2016-17  1610612745               HOU         Houston Rockets   
22     2016-17  1610612744               GSW   Golden State Warriors   
23     2016-17  1610612753               ORL           Orlando Magic   
24     2016-17  1610612739               CLE     Cleveland Cavaliers   
17     2016-17  1610612756               PHX            Phoenix Suns   
17     2016-17  1610612748               MIA              Miami Heat   
18     2016-17  1610612751               BKN           Brooklyn Nets   
20     2016-17  1610612742               DAL        Dallas Mavericks   
21     2016-17  1610612760               OKC   Oklahoma City Thunder   
22     2016-17  1610612761               TOR         Toronto Raptors   
23     2016-17  1610612762               UTA               Utah Jazz   
24     2016-17  1610612765               DET         Detroit Pistons   
19     2016-17  1610612740               NOP    New Orleans Pelicans   

     GAME_ID   GAME_DATE      MATCHUP WL   MIN       FGM  ...      PTS-  \
0   21600001  2016-10-25  CLE vs. NYK  W  48.0  0.937500  ...  1.833333   
2   21600001  2016-10-25    NYK @ CLE  L  48.0  0.666667  ...  2.437500   
1   21600003  2016-10-25    SAS @ GSW  W  48.0  0.979167  ...  2.083333   
0   21600002  2016-10-25    UT

In [62]:
def getRestDays(team, opp, gameDate, year):
    teamGames = games[year][games[year]['TEAM_ABBREVIATION']==team].copy()
    oppGames = games[year][games[year]['TEAM_ABBREVIATION']==opp].copy()
    teamGames['GAME_DATE'] = pd.to_datetime(teamGames['GAME_DATE'])
    oppGames['GAME_DATE'] = pd.to_datetime(oppGames['GAME_DATE'])
    
    past14 = (pd.to_datetime(gameDate) - pd.to_timedelta(14, unit='days')).round(freq='H')
    past28 = (pd.to_datetime(gameDate) - pd.to_timedelta(28, unit='days')).round(freq='H')
    
    team14 = teamGames[(teamGames['GAME_DATE'] < gameDate) & (teamGames['GAME_DATE'] >= str(past14))]
    team28 = teamGames[(teamGames['GAME_DATE'] < gameDate) & (teamGames['GAME_DATE'] >= str(past28))]
    opp14 = oppGames[(oppGames['GAME_DATE'] < gameDate) & (oppGames['GAME_DATE'] >= str(past14))]
    opp28 = oppGames[(oppGames['GAME_DATE'] < gameDate) & (oppGames['GAME_DATE'] >= str(past28))]
    
    teamLast = teamGames[teamGames['GAME_DATE'] < gameDate]['GAME_DATE'].max()
    teamSince = 0
    if (not pd.isna(teamLast)):
        teamSince = (pd.to_datetime(gameDate) - pd.to_datetime(teamLast)).days
    oppLast = oppGames[oppGames['GAME_DATE'] < gameDate]['GAME_DATE'].max()
    oppSince = 0
    if (not pd.isna(oppLast)):
        oppSince = (pd.to_datetime(gameDate) - pd.to_datetime(oppLast)).days
    #print(str(teamSince) + '    ' + str(oppSince))
    toreturn = pd.Series([teamSince, 14-len(team14), 28-len(team28), oppSince, 14-len(opp14), 28-len(opp28)])
    print(toreturn)
    return toreturn

In [63]:
for i in range(0,len(games)):
    games[i][['REST_RECENT','REST_14','REST_28','REST_RECENT-','REST_14-','REST_28-']] = games[i].apply(lambda x: getRestDays(x['TEAM_ABBREVIATION'], x['TEAM_ABBREVIATION-'], x['GAME_DATE'], i), axis = 1)

0     0
1    14
2    28
3     0
4    14
5    28
dtype: int64
0     0
1    14
2    28
3     0
4    14
5    28
dtype: int64
0     0
1    14
2    28
3     0
4    14
5    28
dtype: int64
0     0
1    14
2    28
3     0
4    14
5    28
dtype: int64
0     0
1    14
2    28
3     0
4    14
5    28
dtype: int64
0     0
1    14
2    28
3     0
4    14
5    28
dtype: int64
0     0
1    14
2    28
3     0
4    14
5    28
dtype: int64
0     0
1    14
2    28
3     0
4    14
5    28
dtype: int64
0     0
1    14
2    28
3     0
4    14
5    28
dtype: int64
0     0
1    14
2    28
3     0
4    14
5    28
dtype: int64
0     0
1    14
2    28
3     0
4    14
5    28
dtype: int64
0     0
1    14
2    28
3     0
4    14
5    28
dtype: int64
0     0
1    14
2    28
3     0
4    14
5    28
dtype: int64
0     0
1    14
2    28
3     0
4    14
5    28
dtype: int64
0     0
1    14
2    28
3     0
4    14
5    28
dtype: int64
0     1
1    13
2    27
3     0
4    14
5    28
dtype: int64
0     0
1    14
2    28


0     2
1     9
2    23
3     2
4    10
5    24
dtype: int64
0     2
1    10
2    24
3     2
4    10
5    24
dtype: int64
0     2
1     9
2    23
3     2
4     9
5    23
dtype: int64
0     2
1     9
2    23
3     3
4     9
5    23
dtype: int64
0     1
1     9
2    23
3     2
4     9
5    23
dtype: int64
0     2
1     9
2    23
3     2
4    10
5    24
dtype: int64
0     2
1     9
2    23
3     2
4    11
5    25
dtype: int64
0     2
1     9
2    23
3     2
4     9
5    23
dtype: int64
0     2
1     9
2    23
3     1
4     9
5    23
dtype: int64
0     2
1    10
2    24
3     2
4     9
5    23
dtype: int64
0     2
1     9
2    23
3     2
4     9
5    23
dtype: int64
0     3
1     9
2    23
3     2
4     9
5    23
dtype: int64
0     1
1     8
2    22
3     1
4     9
5    23
dtype: int64
0     1
1     9
2    23
3     3
4     9
5    23
dtype: int64
0     3
1    10
2    24
3     2
4     8
5    22
dtype: int64
0     4
1    10
2    24
3     2
4    10
5    24
dtype: int64
0     2
1    10
2    24


0     2
1     9
2    20
3     2
4     7
5    18
dtype: int64
0     2
1     7
2    18
3     2
4     7
5    18
dtype: int64
0     2
1     6
2    17
3     2
4     7
5    18
dtype: int64
0     1
1     7
2    18
3     2
4     7
5    19
dtype: int64
0     2
1     7
2    18
3     3
4     8
5    20
dtype: int64
0     3
1     8
2    19
3     2
4     7
5    19
dtype: int64
0     3
1     8
2    20
3     2
4     7
5    18
dtype: int64
0     2
1     7
2    19
3     1
4     7
5    18
dtype: int64
0     1
1     7
2    19
3     2
4     8
5    20
dtype: int64
0     2
1     7
2    18
3     2
4     6
5    17
dtype: int64
0     2
1     8
2    18
3     3
4     7
5    19
dtype: int64
0     1
1     8
2    19
3     3
4     8
5    18
dtype: int64
0     3
1     8
2    18
3     1
4     8
5    19
dtype: int64
0     3
1     7
2    17
3     2
4     7
5    17
dtype: int64
0     3
1     7
2    19
3     2
4     8
5    18
dtype: int64
0     2
1     6
2    17
3     2
4     7
5    18
dtype: int64
0     2
1     7
2    17


0     3
1     8
2    16
3     2
4     8
5    16
dtype: int64
0     2
1     7
2    14
3     2
4     8
5    14
dtype: int64
0     2
1     7
2    14
3     2
4     7
5    14
dtype: int64
0     5
1     9
2    17
3     3
4     8
5    14
dtype: int64
0     2
1     7
2    16
3     2
4     7
5    15
dtype: int64
0     2
1     7
2    15
3     2
4     8
5    18
dtype: int64
0     2
1     8
2    14
3     2
4     8
5    14
dtype: int64
0     2
1     8
2    14
3     2
4     7
5    14
dtype: int64
0     2
1     7
2    15
3     2
4     6
5    13
dtype: int64
0     2
1     8
2    14
3     2
4     6
5    13
dtype: int64
0     2
1     8
2    16
3     3
4     8
5    16
dtype: int64
0     2
1     6
2    13
3     2
4     8
5    15
dtype: int64
0     2
1     6
2    13
3     2
4     8
5    14
dtype: int64
0     2
1     8
2    14
3     2
4     7
5    15
dtype: int64
0     2
1     8
2    18
3     2
4     7
5    15
dtype: int64
0     2
1     6
2    14
3     2
4     6
5    13
dtype: int64
0     3
1     8
2    14


dtype: int64
0     2
1     7
2    15
3     2
4     7
5    14
dtype: int64
0     2
1     8
2    16
3     2
4     8
5    15
dtype: int64
0     1
1     8
2    15
3     2
4     7
5    13
dtype: int64
0     2
1     7
2    13
3     1
4     8
5    15
dtype: int64
0     2
1     7
2    14
3     3
4     7
5    15
dtype: int64
0     1
1     7
2    13
3     2
4     9
5    15
dtype: int64
0     1
1     6
2    14
3     3
4     7
5    15
dtype: int64
0     2
1     7
2    15
3     2
4     7
5    16
dtype: int64
0     2
1     7
2    14
3     2
4     7
5    15
dtype: int64
0     1
1     7
2    14
3     3
4     7
5    15
dtype: int64
0     3
1     8
2    15
3     3
4     9
5    16
dtype: int64
0     3
1     7
2    15
3     1
4     7
5    14
dtype: int64
0     3
1     7
2    15
3     1
4     6
5    14
dtype: int64
0     2
1     7
2    15
3     3
4     8
5    15
dtype: int64
0     3
1     9
2    16
3     3
4     8
5    15
dtype: int64
0     3
1     8
2    15
3     2
4     7
5    15
dtype: int64
0     1
1  

...

0     1
1     6
2    12
3     1
4     6
5    13
dtype: int64
0     2
1     6
2    12
3     1
4     7
5    14
dtype: int64
0     2
1     7
2    14
3     1
4     6
5    13
dtype: int64
0     3
1     7
2    14
3     2
4     7
5    14
dtype: int64
0     2
1     6
2    13
3     2
4     6
5    12
dtype: int64
0     2
1     6
2    14
3     2
4     7
5    14
dtype: int64
0     2
1     6
2    13
3     3
4     7
5    13
dtype: int64
0     1
1     7
2    13
3     2
4     7
5    14
dtype: int64
0     2
1     7
2    13
3     1
4     6
5    13
dtype: int64
0     3
1     8
2    14
3     1
4     7
5    13
dtype: int64
0     2
1     7
2    14
3     2
4     7
5    13
dtype: int64
0     2
1     7
2    14
3     1
4     7
5    13
dtype: int64
0     3
1     7
2    13
3     2
4     6
5    13
dtype: int64
0     2
1     7
2    13
3     2
4     8
5    13
dtype: int64
0     2
1     7
2    13
3     2
4     7
5    14
dtype: int64
0     2
1     8
2    13
3     2
4     7
5    13
dtype: int64
0     1
1     6
2    13


0     2
1     6
2    14
3     2
4     6
5    13
dtype: int64
0     2
1     7
2    13
3     2
4     6
5    12
dtype: int64
0     2
1     8
2    14
3     2
4     6
5    13
dtype: int64
0     2
1     7
2    14
3     2
4     7
5    13
dtype: int64
0     2
1     7
2    14
3     2
4     7
5    13
dtype: int64
0     2
1     7
2    13
3     1
4     6
5    12
dtype: int64
0     2
1     7
2    13
3     1
4     6
5    12
dtype: int64
0     2
1     7
2    13
3     2
4     7
5    14
dtype: int64
0     2
1     7
2    13
3     1
4     6
5    13
dtype: int64
0     1
1     6
2    13
3     2
4     7
5    14
dtype: int64
0     1
1     6
2    13
3     1
4     6
5    13
dtype: int64
0     1
1     6
2    12
3     2
4     7
5    13
dtype: int64
0     1
1     6
2    13
3     2
4     7
5    13
dtype: int64
0     1
1     6
2    12
3     2
4     7
5    13
dtype: int64
0     1
1     6
2    13
3     1
4     6
5    13
dtype: int64
0     2
1     7
2    14
3     1
4     6
5    13
dtype: int64
0     2
1     6
2    12


0     2
1     7
2    13
3     3
4     7
5    13
dtype: int64
0     1
1     6
2    12
3     2
4     6
5    12
dtype: int64
0     1
1     7
2    14
3     2
4     7
5    13
dtype: int64
0     3
1     7
2    13
3     2
4     7
5    13
dtype: int64
0     3
1     7
2    13
3     2
4     7
5    14
dtype: int64
0     1
1     7
2    14
3     2
4     8
5    14
dtype: int64
0     2
1     7
2    13
3     1
4     7
5    14
dtype: int64
0     1
1     6
2    13
3     2
4     7
5    13
dtype: int64
0     1
1     6
2    12
3     2
4     7
5    14
dtype: int64
0     2
1     7
2    13
3     2
4     7
5    13
dtype: int64
0     2
1     7
2    14
3     1
4     7
5    13
dtype: int64
0     3
1     7
2    13
3     1
4     6
5    13
dtype: int64
0     2
1     7
2    14
3     1
4     6
5    13
dtype: int64
0     2
1     6
2    13
3     2
4     7
5    14
dtype: int64
0     2
1     6
2    13
3     2
4     7
5    14
dtype: int64
0     2
1     7
2    14
3     2
4     6
5    13
dtype: int64
0     2
1     6
2    14


0     2
1     7
2    14
3     2
4     6
5    13
dtype: int64
0     1
1     6
2    12
3     2
4     7
5    13
dtype: int64
0     1
1     6
2    12
3     2
4     7
5    13
dtype: int64
0     2
1     7
2    13
3     2
4     7
5    13
dtype: int64
0     3
1     7
2    12
3     2
4     6
5    13
dtype: int64
0     1
1     6
2    13
3     1
4     7
5    13
dtype: int64
0     2
1     7
2    13
3     1
4     6
5    12
dtype: int64
0     2
1     7
2    13
3     1
4     6
5    12
dtype: int64
0     2
1     7
2    13
3     2
4     7
5    13
dtype: int64
0     1
1     7
2    13
3     1
4     6
5    13
dtype: int64
0     2
1     6
2    13
3     3
4     7
5    12
dtype: int64
0     2
1     6
2    13
3     2
4     7
5    14
dtype: int64
0     3
1     7
2    14
3     2
4     9
5    14
dtype: int64
0     2
1     9
2    14
3     3
4     7
5    14
dtype: int64
0     2
1     7
2    14
3     2
4     7
5    12
dtype: int64
0     2
1     7
2    14
3     2
4     6
5    13
dtype: int64
0     2
1     7
2    13


0     2
1     7
2    15
3     2
4     6
5    13
dtype: int64
0     2
1     6
2    12
3     2
4     7
5    13
dtype: int64
0     2
1     6
2    13
3     3
4     7
5    14
dtype: int64
0     3
1     8
2    14
3     2
4     7
5    13
dtype: int64
0     2
1     8
2    15
3     3
4     8
5    14
dtype: int64
0     2
1     7
2    13
3     2
4     7
5    14
dtype: int64
0     2
1     7
2    14
3     2
4     7
5    13
dtype: int64
0     2
1     7
2    13
3     3
4     8
5    14
dtype: int64
0     1
1     6
2    12
3     2
4     7
5    13
dtype: int64
0     2
1     7
2    14
3     2
4     6
5    13
dtype: int64
0     1
1     7
2    13
3     2
4     7
5    14
dtype: int64
0     2
1     7
2    13
3     3
4     6
5    12
dtype: int64
0     1
1     6
2    13
3     1
4     7
5    13
dtype: int64
0     2
1     7
2    13
3     1
4     7
5    13
dtype: int64
0     2
1     7
2    13
3     2
4     6
5    13
dtype: int64
0     1
1     6
2    14
3     2
4     7
5    13
dtype: int64
0     2
1     6
2    12


In [64]:
def getTravellingDays(team, opp, gameDate, year):
    teamGames = games[year][games[year]['TEAM_ABBREVIATION']==team].copy()
    oppGames = games[year][games[year]['TEAM_ABBREVIATION']==opp].copy()
    teamGames['GAME_DATE'] = pd.to_datetime(teamGames['GAME_DATE'])
    oppGames['GAME_DATE'] = pd.to_datetime(oppGames['GAME_DATE'])
    
    past14 = (pd.to_datetime(gameDate) - pd.to_timedelta(14, unit='days')).round(freq='H')
    past28 = (pd.to_datetime(gameDate) - pd.to_timedelta(28, unit='days')).round(freq='H')
    
    team14 = teamGames[(teamGames['GAME_DATE'] < gameDate) & (teamGames['GAME_DATE'] >= str(past14))]
    team28 = teamGames[(teamGames['GAME_DATE'] < gameDate) & (teamGames['GAME_DATE'] >= str(past28))]
    opp14 = oppGames[(oppGames['GAME_DATE'] < gameDate) & (oppGames['GAME_DATE'] >= str(past14))]
    opp28 = oppGames[(oppGames['GAME_DATE'] < gameDate) & (oppGames['GAME_DATE'] >= str(past28))]
    
    team14['TRAV'] = (team14['MATCHUP'].str.contains('vs.')*1).diff()
    team14['TRAV_DAYS'] = team14['GAME_DATE'].diff().dt.days
    team14['TRAV_DAYS'][(team14['MATCHUP'].str.contains('vs.') & (team14['TRAV'] == 0))] = 0
    team28['TRAV'] = (team28['MATCHUP'].str.contains('vs.')*1).diff()
    team28['TRAV_DAYS'] = team28['GAME_DATE'].diff().dt.days
    team28['TRAV_DAYS'][(team28['MATCHUP'].str.contains('vs.') & (team28['TRAV'] == 0))] = 0
    
    opp14['TRAV'] = (opp14['MATCHUP'].str.contains('vs.')*1).diff()
    opp14['TRAV_DAYS'] = opp14['GAME_DATE'].diff().dt.days
    opp14['TRAV_DAYS'][(opp14['MATCHUP'].str.contains('vs.') & (opp14['TRAV'] == 0))] = 0
    opp28['TRAV'] = (opp28['MATCHUP'].str.contains('vs.')*1).diff()
    opp28['TRAV_DAYS'] = opp28['GAME_DATE'].diff().dt.days
    opp28['TRAV_DAYS'][(opp28['MATCHUP'].str.contains('vs.') & (opp28['TRAV'] == 0))] = 0
    #team14['TRAV_DAYS'] = [x['TRAV_DAYS'] if (((x['MATCHUP'].str.contains('@')) and (x['TRAV_DAYS'] == 0)) or (x['TRAV_DAYS']  != 0)) else 0 for x in team14]
    #team14['TRAV_DAYS'] = team14['TRAV_DAYS'].apply()
    #print(team14['TRAV_DAYS'])
    #print(str(teamSince) + '    ' + str(oppSince))
    #toreturn = pd.Series([len(team14['TRAV_DAYS'][team14['TRAV_DAYS'] > 0]), len(team28['TRAV_DAYS'][team28['TRAV_DAYS'] > 0]), len(opp14['TRAV_DAYS'][opp14['TRAV_DAYS'] > 0]), len(opp28['TRAV_DAYS'][opp28['TRAV_DAYS'] > 0])])
    toreturn = pd.Series([team14['TRAV_DAYS'].sum(), team28['TRAV_DAYS'].sum(), opp14['TRAV_DAYS'].sum(), opp28['TRAV_DAYS'].sum()])

    print(toreturn)
    return toreturn

In [65]:
for i in range(0,len(games)):
    games[i][['TRAV_DAYS_14', 'TRAV_DAYS_28', 'TRAV_DAYS_14-', 'TRAV_DAYS_28-']] = games[i].apply(lambda x: getTravellingDays(x['TEAM_ABBREVIATION'], x['TEAM_ABBREVIATION-'], x['GAME_DATE'], i), axis = 1)

C:\Users\Kyle\anaconda3\lib\site-packages\ipykernel_launcher.py:17: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
C:\Users\Kyle\anaconda3\lib\site-packages\pandas\core\generic.py:8767: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self._update_inplace(new_data)
C:\Users\Kyle\anaconda3\lib\site-packages\ipykernel_launcher.py:20: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
C:\Users\Kyle\anaconda3\lib\site-packages\ipykernel_launcher.py:24:

0    0
1    0
2    0
3    0
dtype: int64
0    0
1    0
2    0
3    0
dtype: int64
0    0
1    0
2    0
3    0
dtype: int64
0    0
1    0
2    0
3    0
dtype: int64
0    0
1    0
2    0
3    0
dtype: int64
0    0
1    0
2    0
3    0
dtype: int64
0    0
1    0
2    0
3    0
dtype: int64
0    0
1    0
2    0
3    0
dtype: int64
0    0
1    0
2    0
3    0
dtype: int64
0    0
1    0
2    0
3    0
dtype: int64
0    0
1    0
2    0
3    0
dtype: int64
0    0
1    0
2    0
3    0
dtype: int64
0    0
1    0
2    0
3    0
dtype: int64
0    0
1    0
2    0
3    0
dtype: int64
0    0
1    0
2    0
3    0
dtype: int64
0    0.0
1    0.0
2    0.0
3    0.0
dtype: float64
0    0
1    0
2    0
3    0
dtype: int64
0    0.0
1    0.0
2    0.0
3    0.0
dtype: float64
0    0
1    0
2    0
3    0
dtype: int64
0    0
1    0
2    0
3    0
dtype: int64

C:\Users\Kyle\anaconda3\lib\site-packages\ipykernel_launcher.py:15: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  from ipykernel import kernelapp as app
C:\Users\Kyle\anaconda3\lib\site-packages\ipykernel_launcher.py:16: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  app.launch_new_instance()
C:\Users\Kyle\anaconda3\lib\site-packages\ipykernel_launcher.py:18: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

Se


0    0.0
1    0.0
2    0.0
3    0.0
dtype: float64
0    0
1    0
2    0
3    0
dtype: int64
0    0
1    0
2    0
3    0
dtype: int64
0    0
1    0
2    0
3    0
dtype: int64
0    0.0
1    0.0
2    0.0
3    0.0
dtype: float64
0    0
1    0
2    0
3    0
dtype: int64
0    0
1    0
2    0
3    0
dtype: int64
0    0
1    0
2    0
3    0
dtype: int64
0    0
1    0
2    0
3    0
dtype: int64
0    0
1    0
2    0
3    0
dtype: int64
0    0
1    0
2    0
3    0
dtype: int64
0    0.0
1    0.0
2    0.0
3    0.0
dtype: float64
0    0.0
1    0.0
2    0.0
3    0.0
dtype: float64
0    0.0
1    0.0
2    0.0
3    0.0
dtype: float64
0    0.0
1    0.0
2    0.0
3    0.0
dtype: float64
0    0.0
1    0.0
2    0.0
3    0.0
dtype: float64
0    0.0
1    0.0
2    0.0
3    0.0
dtype: float64
0    0.0
1    0.0
2    0.0
3    0.0
dtype: float64
0    0.0
1    0.0
2    0.0
3    0.0
dtype: float64
0    0.0
1    0.0
2    0.0
3    0.0
dtype: float64
0    0.0
1    0.0
2    0.0
3    0.0
dtype: float64
0    0.0
1    0.0


0    6.0
1    6.0
2    9.0
3    9.0
dtype: float64
0    3.0
1    3.0
2    7.0
3    7.0
dtype: float64
0    7.0
1    7.0
2    3.0
3    3.0
dtype: float64
0    9.0
1    9.0
2    7.0
3    7.0
dtype: float64
0     5.0
1     5.0
2    10.0
3    10.0
dtype: float64
0    5.0
1    5.0
2    8.0
3    8.0
dtype: float64
0    3.0
1    3.0
2    9.0
3    9.0
dtype: float64
0    4.0
1    4.0
2    7.0
3    7.0
dtype: float64
0    9.0
1    9.0
2    3.0
3    3.0
dtype: float64
0    10.0
1    10.0
2     3.0
3     3.0
dtype: float64
0    8.0
1    8.0
2    7.0
3    7.0
dtype: float64
0    8.0
1    8.0
2    9.0
3    9.0
dtype: float64
0    11.0
1    11.0
2     8.0
3     8.0
dtype: float64
0     8.0
1     8.0
2    11.0
3    11.0
dtype: float64
0     3.0
1     3.0
2    10.0
3    10.0
dtype: float64
0    9.0
1    9.0
2    8.0
3    8.0
dtype: float64
0    7.0
1    7.0
2    8.0
3    8.0
dtype: float64
0     8.0
1     8.0
2    10.0
3    10.0
dtype: float64
0    10.0
1    10.0
2     8.0
3     8.0
dtype: float64
0  

...

0     8.0
1    22.0
2     6.0
3    18.0
dtype: float64
0     7.0
1    12.0
2     6.0
3    21.0
dtype: float64
0    12.0
1    24.0
2     5.0
3    10.0
dtype: float64
0     7.0
1    16.0
2     5.0
3    21.0
dtype: float64
0     7.0
1    11.0
2     9.0
3    16.0
dtype: float64
0     7.0
1    12.0
2    10.0
3    13.0
dtype: float64
0     6.0
1    21.0
2     7.0
3    21.0
dtype: float64
0     5.0
1    21.0
2     7.0
3    16.0
dtype: float64
0     3.0
1    18.0
2    12.0
3    18.0
dtype: float64
0    10.0
1    13.0
2     7.0
3    12.0
dtype: float64
0     7.0
1    21.0
2     6.0
3    21.0
dtype: float64
0     9.0
1    17.0
2    10.0
3    23.0
dtype: float64
0    10.0
1    13.0
2    10.0
3    14.0
dtype: float64
0     9.0
1    16.0
2     7.0
3    11.0
dtype: float64
0    12.0
1    18.0
2     3.0
3    18.0
dtype: float64
0    10.0
1    14.0
2    10.0
3    13.0
dtype: float64
0    10.0
1    23.0
2     9.0
3    17.0
dtype: float64
0     4.0
1    13.0
2     8.0
3    13.0
dtype: float64
0     3.0


0    10.0
1    13.0
2     8.0
3    19.0
dtype: float64
0     9.0
1    19.0
2    11.0
3    22.0
dtype: float64
0    10.0
1    19.0
2     8.0
3    15.0
dtype: float64
0     7.0
1    19.0
2    10.0
3    18.0
dtype: float64
0     5.0
1    16.0
2    12.0
3    20.0
dtype: float64
0     4.0
1    18.0
2     8.0
3    14.0
dtype: float64
0    10.0
1    18.0
2     7.0
3    19.0
dtype: float64
0     8.0
1    15.0
2    10.0
3    19.0
dtype: float64
0     5.0
1    15.0
2    12.0
3    19.0
dtype: float64
0     8.0
1    19.0
2    10.0
3    13.0
dtype: float64
0    12.0
1    20.0
2     5.0
3    16.0
dtype: float64
0     3.0
1    12.0
2    12.0
3    19.0
dtype: float64
0     0.0
1    13.0
2     5.0
3    12.0
dtype: float64
0    11.0
1    21.0
2    11.0
3    21.0
dtype: float64
0    10.0
1    21.0
2    12.0
3    22.0
dtype: float64
0     8.0
1    22.0
2     9.0
3    19.0
dtype: float64
0     7.0
1    19.0
2     0.0
3    11.0
dtype: float64
0     7.0
1    17.0
2    11.0
3    18.0
dtype: float64
0     4.0


0    10.0
1    17.0
2    11.0
3    25.0
dtype: float64
0    10.0
1    17.0
2     9.0
3    20.0
dtype: float64
0    11.0
1    21.0
2     8.0
3    15.0
dtype: float64
0     5.0
1    16.0
2     8.0
3    21.0
dtype: float64
0     8.0
1    15.0
2    11.0
3    21.0
dtype: float64
0     6.0
1    17.0
2    10.0
3    21.0
dtype: float64
0     8.0
1    18.0
2    10.0
3    19.0
dtype: float64
0     6.0
1    18.0
2     6.0
3    17.0
dtype: float64
0     8.0
1    20.0
2     8.0
3    21.0
dtype: float64
0     9.0
1    22.0
2     7.0
3    10.0
dtype: float64
0     8.0
1    21.0
2     8.0
3    20.0
dtype: float64
0     6.0
1    17.0
2     6.0
3    18.0
dtype: float64
0    10.0
1    21.0
2     6.0
3    17.0
dtype: float64
0     7.0
1    10.0
2     9.0
3    22.0
dtype: float64
0    10.0
1    19.0
2     8.0
3    18.0
dtype: float64
0    12.0
1    23.0
2     9.0
3    14.0
dtype: float64
0     8.0
1    21.0
2     6.0
3    17.0
dtype: float64
0     9.0
1    19.0
2     5.0
3    19.0
dtype: float64
0     9.0


0    11.0
1    20.0
2    10.0
3    22.0
dtype: float64
0     3.0
1    13.0
2    10.0
3    21.0
dtype: float64
0     5.0
1    18.0
2     9.0
3    18.0
dtype: float64
0     9.0
1    19.0
2     6.0
3    19.0
dtype: float64
0     5.0
1    10.0
2     8.0
3    16.0
dtype: float64
0    10.0
1    22.0
2    11.0
3    20.0
dtype: float64
0     8.0
1    16.0
2     5.0
3    10.0
dtype: float64
0    11.0
1    20.0
2     8.0
3    16.0
dtype: float64
0     6.0
1    14.0
2     5.0
3    15.0
dtype: float64
0     5.0
1    20.0
2    11.0
3    23.0
dtype: float64
0    12.0
1    17.0
2    11.0
3    19.0
dtype: float64
0     7.0
1    22.0
2     9.0
3    22.0
dtype: float64
0    11.0
1    22.0
2     5.0
3    13.0
dtype: float64
0     4.0
1    17.0
2    11.0
3    24.0
dtype: float64
0     8.0
1    16.0
2    12.0
3    23.0
dtype: float64
0    11.0
1    18.0
2     7.0
3    17.0
dtype: float64
0     7.0
1    17.0
2    11.0
3    18.0
dtype: float64
0     9.0
1    22.0
2     7.0
3    22.0
dtype: float64
0    11.0


0     5.0
1    21.0
2     9.0
3    20.0
dtype: float64
0     5.0
1    19.0
2     9.0
3    15.0
dtype: float64
0     7.0
1    16.0
2     6.0
3    18.0
dtype: float64
0    10.0
1    22.0
2     7.0
3    20.0
dtype: float64
0     8.0
1    18.0
2    10.0
3    18.0
dtype: float64
0     6.0
1    19.0
2    11.0
3    23.0
dtype: float64
0    11.0
1    21.0
2     5.0
3    15.0
dtype: float64
0     5.0
1    20.0
2     9.0
3    15.0
dtype: float64
0     8.0
1    17.0
2    10.0
3    21.0
dtype: float64
0    10.0
1    18.0
2     8.0
3    18.0
dtype: float64
0     6.0
1    18.0
2     7.0
3    16.0
dtype: float64
0     5.0
1    15.0
2    11.0
3    21.0
dtype: float64
0     9.0
1    15.0
2     5.0
3    19.0
dtype: float64
0    10.0
1    21.0
2     8.0
3    17.0
dtype: float64
0    11.0
1    23.0
2     6.0
3    19.0
dtype: float64
0     9.0
1    15.0
2     5.0
3    20.0
dtype: float64
0     7.0
1    20.0
2    10.0
3    22.0
dtype: float64
0     5.0
1    11.0
2    12.0
3    25.0
dtype: float64
0     6.0


In [66]:
for i in range(0, len(games)):
    games[i]['REST_RECENT_DIFF']=games[i]['REST_RECENT']-games[i]['REST_RECENT-']
    games[i]['REST_14_DIFF']=games[i]['REST_14']-games[i]['REST_14-']
    games[i]['REST_28_DIFF']=games[i]['REST_28']-games[i]['REST_28-']
    games[i]['TRAV_DAYS_14_DIFF'] = games[i]['TRAV_DAYS_14']-games[i]['TRAV_DAYS_14-']
    games[i]['TRAV_DAYS_28_DIFF'] = games[i]['TRAV_DAYS_28']-games[i]['TRAV_DAYS_28-']
    
train = pd.concat([games[0],games[1],games[2],games[3]])
home = train[train['MATCHUP'].str.contains('vs.')].copy()
away = train[train['MATCHUP'].str.contains('@')].copy()

train.head()

SEASON_YEAR     TEAM_ID TEAM_ABBREVIATION             TEAM_NAME   GAME_ID  \
0     2014-15  1610612747               LAL    Los Angeles Lakers  21400003   
1     2014-15  1610612759               SAS     San Antonio Spurs  21400002   
2     2014-15  1610612740               NOP  New Orleans Pelicans  21400001   
1     2014-15  1610612753               ORL         Orlando Magic  21400001   
2     2014-15  1610612745               HOU       Houston Rockets  21400003   

    GAME_DATE      MATCHUP WL   MIN       FGM  ...  REST_28-  TRAV_DAYS_14  \
0  2014-10-28  LAL vs. HOU  L  48.0  0.583333  ...        28           0.0   
1  2014-10-28  SAS vs. DAL  W  48.0  0.770833  ...        28           0.0   
2  2014-10-28  NOP vs. ORL  W  48.0  0.854167  ...        28           0.0   
1  2014-10-28    ORL @ NOP  L  48.0  0.666667  ...        28           0.0   
2  2014-10-28    HOU @ LAL  W  48.0  0.645833  ...        28           0.0   

   TRAV_DAYS_28  TRAV_DAYS_14-  TRAV_DAYS_28-  REST_RECENT_DIFF  REST_14_DIFF  \
0           0.0            0.0            0.0                 0             0   
1           0.0            0.0            0.0                 0             0   
2           0.0            0.0            0.0                 0             0   
1           0.0            0.0            0.0                 0             0   
2           0.0            0.0            0.0                 0             0   

   REST_28_DIFF  TRAV_DAYS_14_DIFF  TRAV_DAYS_28_DIFF  
0             0                0.0                0.0  
1             0                0.0                0.0  
2             0                0.0                0.0  
1             0                0.0                0.0  
2             0                0.0                0.0  

[5 rows x 84 columns]

In [67]:
priors = {}
priors['Whome'] = len(train[(train['WL'] == 'W') & (train['MATCHUP'].str.contains('vs.'))])/len(train[train['WL'] == 'W'])
priors['Waway'] = len(train[(train['WL'] == 'W') & (train['MATCHUP'].str.contains('@'))])/len(train[train['WL'] == 'W'])
priors['Lhome'] = len(train[(train['WL'] == 'L') & (train['MATCHUP'].str.contains('vs.'))])/len(train[train['WL'] == 'L'])
priors['Laway'] = len(train[(train['WL'] == 'L') & (train['MATCHUP'].str.contains('@'))])/len(train[train['WL'] == 'L'])
for i in train['REST_RECENT_DIFF'].unique():
    priors['WREST_RECENT_DIFF' + str(i)] = len(train[(train['WL'] == 'W') & (train['REST_RECENT_DIFF'] == i)])/len(train[train['WL'] == 'W'])
    priors['LREST_RECENT_DIFF' + str(i)] = len(train[(train['WL'] == 'L') & (train['REST_RECENT_DIFF'] == i)])/len(train[train['WL'] == 'L'])
for i in train['REST_14_DIFF'].unique():
    priors['WREST_14_DIFF' + str(i)] = len(train[(train['WL'] == 'W') & (train['REST_14_DIFF'] == i)])/len(train[train['WL'] == 'W'])
    priors['LREST_14_DIFF' + str(i)] = len(train[(train['WL'] == 'L') & (train['REST_14_DIFF'] == i)])/len(train[train['WL'] == 'L'])
for i in train['TRAV_DAYS_14_DIFF'].unique():
    priors['WTRAV_DAYS_14_DIFF' + str(i)] = len(train[(train['WL'] == 'W') & (train['TRAV_DAYS_14_DIFF'] == i)])/len(train[train['WL'] == 'W'])
    priors['LTRAV_DAYS_14_DIFF' + str(i)] = len(train[(train['WL'] == 'L') & (train['TRAV_DAYS_14_DIFF'] == i)])/len(train[train['WL'] == 'L'])
priors['WWPCT'] = len(train[(train['WL'] == 'W') & (train['WPCT'] > train['WPCT-'])])/len(train[train['WL'] == 'W'])
priors['WWPCT-'] = len(train[(train['WL'] == 'W') & (train['WPCT'] <= train['WPCT-'])])/len(train[train['WL'] == 'W'])
priors['LWPCT'] = len(train[(train['WL'] == 'L') & (train['WPCT'] > train['WPCT-'])])/len(train[train['WL'] == 'L'])
priors['LWPCT-'] = len(train[(train['WL'] == 'L') & (train['WPCT'] <= train['WPCT-'])])/len(train[train['WL'] == 'L'])
print(priors)

{'Whome': 0.5819772172497966, 'Waway': 0.41802278275020344, 'Lhome': 0.4181929181929182, 'Laway': 0.5818070818070818, 'WREST_RECENT_DIFF0': 0.4902359641985354, 'LREST_RECENT_DIFF0': 0.49002849002849, 'WREST_RECENT_DIFF1': 0.21419853539462977, 'LREST_RECENT_DIFF1': 0.17887667887667888, 'WREST_RECENT_DIFF-1': 0.17880390561432058, 'LREST_RECENT_DIFF-1': 0.21428571428571427, 'WREST_RECENT_DIFF-2': 0.041700569568755085, 'LREST_RECENT_DIFF-2': 0.051485551485551485, 'WREST_RECENT_DIFF2': 0.05146460537021969, 'LREST_RECENT_DIFF2': 0.04171754171754172, 'WREST_RECENT_DIFF3': 0.01017087062652563, 'LREST_RECENT_DIFF3': 0.006919006919006919, 'WREST_RECENT_DIFF-3': 0.006916192026037429, 'LREST_RECENT_DIFF-3': 0.010175010175010175, 'WREST_RECENT_DIFF5': 0.0002034174125305126, 'LREST_RECENT_DIFF5': 0.0002035002035002035, 'WREST_RECENT_DIFF-5': 0.0002034174125305126, 'LREST_RECENT_DIFF-5': 0.0002035002035002035, 'WREST_RECENT_DIFF-4': 0.0018307567127746134, 'LREST_RECENT_DIFF-4': 0.0010175010175010174,

In [72]:
def immutableBayes(data):
    print(data)
    #data = data[['WL','WPCT','WPCT-','MATCHUP','REST_RECENT_DIFF','REST_14_DIFF','TRAV_DAYS_14_DIFF']]
    w = 1
    l = 1
    if data['WPCT'] > data['WPCT-']:
        w *= priors['WWPCT']
        l *= priors['LWPCT']
    if data['WPCT'] <= data['WPCT-']:
        w *= priors['WWPCT-']
        l *= priors['LWPCT-']
    if 'vs.' in data['MATCHUP']:
        w *= priors['Whome']
        l *= priors['Lhome']
    else:
        w *= priors['Waway']
        l *= priors['Laway']
    
    wrec = priors.get('WREST_RECENT_DIFF' + str(data['REST_RECENT_DIFF']))
    print(wrec)
    if wrec != None: 
        w *= wrec
    lrec = priors.get('LREST_RECENT_DIFF' + str(data['REST_RECENT_DIFF']))
    print(lrec)
    if lrec != None:
        l *= lrec
    
    w14 = priors.get('WREST_14_DIFF' + str(data['REST_14_DIFF']))
    print(w14)
    if w14 != None:
        w *= w14
    
    l14 = priors.get('LREST_14_DIFF' + str(data['REST_14_DIFF']))
    print(l14)
    if l14 != None:
        l *= l14
        
    w14 = priors.get('WTRAV_DAYS_14_DIFF' + str(data['TRAV_DAYS_14_DIFF']))
    if w14 != None:
        w *= w14
    l14 = priors.get('LTRAV_DAYS_14_DIFF' + str(data['TRAV_DAYS_14_DIFF']))
    if l14 != None:
        l *= l14
    
    print(str(w) + '   ' + str(l))
    
    if (w > l):
        if data['WL'] == 'W':
            return True
        else:
            return False
    else:
        if data['WL'] == 'W':
            return False
        else:
            return True

In [73]:
test = pd.concat([games[4],games[5],games[6]])
test.head()

SEASON_YEAR     TEAM_ID TEAM_ABBREVIATION              TEAM_NAME   GAME_ID  \
0     2018-19  1610612738               BOS         Boston Celtics  21800001   
1     2018-19  1610612744               GSW  Golden State Warriors  21800002   
1     2018-19  1610612755               PHI     Philadelphia 76ers  21800001   
0     2018-19  1610612760               OKC  Oklahoma City Thunder  21800002   
9     2018-19  1610612742               DAL       Dallas Mavericks  21800013   

    GAME_DATE      MATCHUP WL   MIN       FGM  ...  REST_28-  TRAV_DAYS_14  \
0  2018-10-16  BOS vs. PHI  W  48.0  0.875000  ...        28           0.0   
1  2018-10-16  GSW vs. OKC  W  48.0  0.875000  ...        28           0.0   
1  2018-10-16    PHI @ BOS  L  48.0  0.708333  ...        28           0.0   
0  2018-10-16    OKC @ GSW  L  48.0  0.687500  ...        28           0.0   
9  2018-10-17    DAL @ PHX  L  48.0  0.791667  ...        28           0.0   

   TRAV_DAYS_28  TRAV_DAYS_14-  TRAV_DAYS_28-  REST_RECENT_DIFF  REST_14_DIFF  \
0           0.0            0.0            0.0                 0             0   
1           0.0            0.0            0.0                 0             0   
1           0.0            0.0            0.0                 0             0   
0           0.0            0.0            0.0                 0             0   
9           0.0            0.0            0.0                 0             0   

   REST_28_DIFF  TRAV_DAYS_14_DIFF  TRAV_DAYS_28_DIFF  
0             0                0.0                0.0  
1             0                0.0                0.0  
1             0                0.0                0.0  
0             0                0.0                0.0  
9             0                0.0                0.0  

[5 rows x 84 columns]

In [74]:
test = test[['WL','WPCT','WPCT-','MATCHUP','REST_RECENT_DIFF','REST_14_DIFF','TRAV_DAYS_14_DIFF']]
res = []
for i, r in test.iterrows():
    res.append(immutableBayes(r))

WL                             W
WPCT                           1
WPCT-                          0
MATCHUP              BOS vs. PHI
REST_RECENT_DIFF               0
REST_14_DIFF                   0
TRAV_DAYS_14_DIFF              0
Name: 0, dtype: object
0.4902359641985354
0.49002849002849
0.39137510170870626
0.3915343915343915
0.010406075502652441   0.002966055762646581
WL                             W
WPCT                           1
WPCT-                          0
MATCHUP              GSW vs. OKC
REST_RECENT_DIFF               0
REST_14_DIFF                   0
TRAV_DAYS_14_DIFF              0
Name: 1, dtype: object
0.4902359641985354
0.49002849002849
0.39137510170870626
0.3915343915343915
0.010406075502652441   0.002966055762646581
WL                           L
WPCT                         0
WPCT-                        1
MATCHUP              PHI @ BOS
REST_RECENT_DIFF             0
REST_14_DIFF                 0
TRAV_DAYS_14_DIFF            0
Name: 1, dtype: object
0.490235964198

Name: 42, dtype: object
0.4902359641985354
0.49002849002849
0.39137510170870626
0.3915343915343915
0.007474479258284084   0.0041264980172294775
WL                             W
WPCT                        0.75
WPCT-                   0.333333
MATCHUP              GSW vs. PHX
REST_RECENT_DIFF              -1
REST_14_DIFF                  -1
TRAV_DAYS_14_DIFF              2
Name: 39, dtype: object
0.17880390561432058
0.21428571428571427
0.23047192839707079
0.2389092389092389
0.0015744479135310014   0.0004872222367823278
WL                           W
WPCT                       0.5
WPCT-                      0.5
MATCHUP              ORL @ BOS
REST_RECENT_DIFF             0
REST_14_DIFF                 0
TRAV_DAYS_14_DIFF           -3
Name: 40, dtype: object
0.4902359641985354
0.49002849002849
0.39137510170870626
0.3915343915343915
0.0014946622116422965   0.005820891261898659
WL                             W
WPCT                           1
WPCT-                       0.25
MATCHUP         

0.39137510170870626
0.3915343915343915
0.0005938894672343598   0.00011832729466786316
WL                             W
WPCT                    0.428571
WPCT-                   0.285714
MATCHUP              MIN vs. LAL
REST_RECENT_DIFF               1
REST_14_DIFF                   0
TRAV_DAYS_14_DIFF              2
Name: 91, dtype: object
0.21419853539462977
0.17887667887667888
0.39137510170870626
0.3915343915343915
0.0032028968450590572   0.0006665374810975097
WL                             L
WPCT                    0.571429
WPCT-                   0.666667
MATCHUP              IND vs. POR
REST_RECENT_DIFF               0
REST_14_DIFF                  -1
TRAV_DAYS_14_DIFF              5
Name: 92, dtype: object
0.4902359641985354
0.49002849002849
0.23047192839707079
0.2389092389092389
0.0008102734167745059   0.001582138556209951
WL                             W
WPCT                           1
WPCT-                   0.857143
MATCHUP              MIL vs. TOR
REST_RECENT_DIFF           

Name: 132, dtype: object
0.21419853539462977
0.17887667887667888
0.2390154597233523
0.23056573056573057
0.0006833363930291189   0.0017306125953347243
WL                             W
WPCT                    0.222222
WPCT-                        0.3
MATCHUP              WAS vs. NYK
REST_RECENT_DIFF               0
REST_14_DIFF                   0
TRAV_DAYS_14_DIFF              5
Name: 135, dtype: object
0.4902359641985354
0.49002849002849
0.39137510170870626
0.3915343915343915
0.0013759629778236093   0.0025928744311311293
WL                           W
WPCT                       0.9
WPCT-                      0.4
MATCHUP              TOR @ LAL
REST_RECENT_DIFF             1
REST_14_DIFF                 1
TRAV_DAYS_14_DIFF           -5
Name: 136, dtype: object
0.21419853539462977
0.17887667887667888
0.2390154597233523
0.23056573056573057
0.0006719463019154411   0.0002757539435913436
WL                             L
WPCT                         0.4
WPCT-                        0.9
MATCHUP

0.00028405002762789096   0.00012089704916073686
WL                             W
WPCT                    0.416667
WPCT-                   0.571429
MATCHUP              HOU vs. IND
REST_RECENT_DIFF              -1
REST_14_DIFF                   1
TRAV_DAYS_14_DIFF              4
Name: 187, dtype: object
0.17880390561432058
0.21428571428571427
0.2390154597233523
0.23056573056573057
0.00039858345659333296   0.0008619337276105647
WL                             W
WPCT                    0.571429
WPCT-                   0.583333
MATCHUP              SAC vs. SAS
REST_RECENT_DIFF               0
REST_14_DIFF                  -1
TRAV_DAYS_14_DIFF             -2
Name: 189, dtype: object
0.4902359641985354
0.49002849002849
0.23047192839707079
0.2389092389092389
0.0016045808548933562   0.00330810789025717
WL                             W
WPCT                    0.357143
WPCT-                   0.428571
MATCHUP              MIN vs. BKN
REST_RECENT_DIFF               1
REST_14_DIFF                  

...

0.2389092389092389
0.004607656824851287   0.0014578569235644918
WL                             L
WPCT                    0.516667
WPCT-                   0.440678
MATCHUP              BOS vs. CHI
REST_RECENT_DIFF               0
REST_14_DIFF                   1
TRAV_DAYS_14_DIFF              0
Name: 852, dtype: object
0.4902359641985354
0.49002849002849
0.2390154597233523
0.23056573056573057
0.0063550617025034395   0.0017466430244691146
WL                           L
WPCT                  0.338983
WPCT-                 0.305085
MATCHUP              CLE @ DET
REST_RECENT_DIFF             0
REST_14_DIFF                 1
TRAV_DAYS_14_DIFF            1
Name: 854, dtype: object
0.4902359641985354
0.49002849002849
0.2390154597233523
0.23056573056573057
0.003676937965493085   0.001827152488656871
WL                           L
WPCT                  0.258621
WPCT-                 0.525424
MATCHUP              HOU @ MIA
REST_RECENT_DIFF             0
REST_14_DIFF                -1
TRAV_DAYS_14

0.21419853539462977
0.17887667887667888
0.39137510170870626
0.3915343915343915
0.0015577859539091736   0.0021123831222769796
WL                           W
WPCT                  0.483333
WPCT-                      0.3
MATCHUP              IND @ ORL
REST_RECENT_DIFF            -2
REST_14_DIFF                -1
TRAV_DAYS_14_DIFF           -2
Name: 900, dtype: object
0.041700569568755085
0.051485551485551485
0.23047192839707079
0.2389092389092389
0.00023049179682397625   0.0001863602820104189
WL                           L
WPCT                       0.7
WPCT-                 0.672131
MATCHUP              PHX @ BKN
REST_RECENT_DIFF             1
REST_14_DIFF                 0
TRAV_DAYS_14_DIFF           -5
Name: 901, dtype: object
0.21419853539462977
0.17887667887667888
0.39137510170870626
0.3915343915343915
0.0011002763275619648   0.0004682705979432877
WL                           L
WPCT                  0.428571
WPCT-                 0.357143
MATCHUP              CLE @ WAS
REST_RECENT_DI

0.0006303835401245089   0.0021940900526723857
WL                             L
WPCT                        0.25
WPCT-                        0.5
MATCHUP              HOU vs. GSW
REST_RECENT_DIFF               0
REST_14_DIFF                   0
TRAV_DAYS_14_DIFF             -1
Name: 949, dtype: object
0.4902359641985354
0.49002849002849
0.39137510170870626
0.3915343915343915
0.00332806808921868   0.006199327048977154
WL                           L
WPCT                  0.454545
WPCT-                 0.578125
MATCHUP              WAS @ DAL
REST_RECENT_DIFF            -1
REST_14_DIFF                -1
TRAV_DAYS_14_DIFF            1
Name: 947, dtype: object
0.17880390561432058
0.21428571428571427
0.23047192839707079
0.2389092389092389
0.0005500309124264619   0.0021482140037472207
WL                           W
WPCT                  0.446154
WPCT-                  0.30303
MATCHUP              NOP @ MIN
REST_RECENT_DIFF             0
REST_14_DIFF                 0
TRAV_DAYS_14_DIFF          

0.23047192839707079
0.2389092389092389
0.004316745701490004   0.0011141796259941552
WL                           L
WPCT                  0.294118
WPCT-                 0.691176
MATCHUP              DET @ PHI
REST_RECENT_DIFF             1
REST_14_DIFF                 1
TRAV_DAYS_14_DIFF           -3
Name: 1005, dtype: object
0.21419853539462977
0.17887667887667888
0.2390154597233523
0.23056573056573057
0.00039882941570330697   0.0012512575791116644
WL                             L
WPCT                    0.397059
WPCT-                   0.521739
MATCHUP              TOR vs. MEM
REST_RECENT_DIFF               0
REST_14_DIFF                   0
TRAV_DAYS_14_DIFF              2
Name: 1005, dtype: object
0.4902359641985354
0.49002849002849
0.39137510170870626
0.3915343915343915
0.003117945664033794   0.0047378887332487
WL                             W
WPCT                    0.691176
WPCT-                   0.294118
MATCHUP              PHI vs. DET
REST_RECENT_DIFF              -1
REST_14_

Name: 1050, dtype: object
0.4902359641985354
0.49002849002849
0.39137510170870626
0.3915343915343915
0.00028724778660226544   0.0010657969916152473
WL                           L
WPCT                  0.295775
WPCT-                 0.676056
MATCHUP              ORL @ PHI
REST_RECENT_DIFF             0
REST_14_DIFF                 0
TRAV_DAYS_14_DIFF            1
Name: 1051, dtype: object
0.4902359641985354
0.49002849002849
0.39137510170870626
0.3915343915343915
0.002560887046657485   0.008050866505893638
WL                           W
WPCT                  0.661972
WPCT-                  0.28169
MATCHUP              DEN @ DET
REST_RECENT_DIFF            -2
REST_14_DIFF                 0
TRAV_DAYS_14_DIFF            7
Name: 1052, dtype: object
0.041700569568755085
0.051485551485551485
0.39137510170870626
0.3915343915343915
8.665519121284663e-05   6.174694093157594e-05
WL                           L
WPCT                  0.333333
WPCT-                 0.666667
MATCHUP              SAC @ 

In [75]:
print(np.unique(res, return_counts=True))

(array([False,  True]), array([1889, 4670], dtype=int64))


In [73]:
len(test)

6559